#  Unit 4.3a Parallel Computing
> Observe an algorithm using parallel computing in Python Code.  Monitor processes on host.
- toc: true

## Analyzing Parallel Computing
> Once again we will use image lab, this time to review Parallel Computing.
- Change baseWidth in this line in code to increase computation requirements: ```def process_image(image, baseWidth=512):```  For instance 320, 512, 1024, 2048, 4096.
- Compare Sequential and Parallel computing code and time to achieve outputs

In [52]:
from IPython.display import HTML, display
from pathlib import Path  # https://medium.com/@ageitgey/python-3-quick-tip-the-easy-way-to-deal-with-file-paths-on-windows-mac-and-linux-11a072b58d5f
from PIL import Image as pilImage # as PIL Image is used to avoid conflicts
from io import BytesIO
import base64
import numpy as np


# prepares a series of images
def image_data(path=Path("images/"), images=None):  # path of static images is defaulted
    if images is None:  # default image
        images = [
            {'source': "Internet", 'label': "Green Square", 'file': "green-square-16.png"},
            {'source': "Peter Carolin", 'label': "Clouds Impression", 'file': "clouds-impression.png"},
            {'source': "Peter Carolin", 'label': "Lassen Volcano", 'file': "lassen-volcano.jpg"}
        ]
    for image in images:
        # File to open
        image['filename'] = path / image['file']  # file with path
    return images

# Scale to baseWidth
def scale_image(img, baseWidth):
    scalePercent = (baseWidth/float(img.size[0]))
    scaleHeight = int((float(img.size[1])*float(scalePercent)))
    scale = (baseWidth, scaleHeight)
    return img.resize(scale)

# PIL image converted to base64
def image_to_base64(img, format):
    with BytesIO() as buffer:
        img.save(buffer, format)
        return base64.b64encode(buffer.getvalue()).decode()
    
# Convert pixels to Grey Scale
def grey_pixel(pixel):
    average = (pixel[0] + pixel[1] + pixel[2]) // 3  # average pixel values and use // for integer division
    if len(pixel) > 3:
        return( (average, average, average, pixel[3]) ) # PNG format
    else:
        return( (average, average, average) )
    
# Convert pixels to Red Scale
def red_pixel(pixel):
    if len(pixel) > 3:
        return( (pixel[0], 0, 0, pixel[3]) ) # PNG format
    else:
        return( (pixel[0], 0, 0) )
    
# Convert pixels to Red Scale
def green_pixel(pixel):
    if len(pixel) > 3:
        return( (0, pixel[1], 0, pixel[3]) ) # PNG format
    else:
        return( (0, pixel[1], 0) )
    
# Convert pixels to Red Scale
def blue_pixel(pixel):
    if len(pixel) > 3:
        return( (0, 0, pixel[2], pixel[3]) ) # PNG format
    else:
        return( (0, 0, pixel[2]) )
        
# Set Properties of Image, Scale, and convert to Base64
def image_management(image, baseWidth):  # path of static images is defaulted        
    # Image open return PIL image object
    img = pilImage.open(image['filename'])
    
    # Python Image Library operations
    image['format'] = img.format
    image['mode'] = img.mode
    image['size'] = img.size
    # Scale the Image
    img = scale_image(img, baseWidth)
    image['pil'] = img
    image['scaled_size'] = img.size
    image['numpy'] = np.array(img.getdata())
    # Scaled HTML
    image['html'] = '<img src="data:image/png;base64,%s">' % image_to_base64(image['pil'], image['format'])
    
    # Grey HTML
    # each pixel in numpy array is turned to grey 
    # then resulting list, using List Comprehension, is put back into img    
    img.putdata([grey_pixel(pixel) for pixel in image['numpy']])
    image['html_grey'] =  '<img src="data:image/png;base64,%s">' % image_to_base64(img, image['format'])
    
    # Red HTML
    img.putdata([red_pixel(pixel) for pixel in image['numpy']])
    image['html_red'] =  '<img src="data:image/png;base64,%s">' % image_to_base64(img, image['format'])
    
    # Green HTML
    img.putdata([green_pixel(pixel) for pixel in image['numpy']])
    image['html_green'] =  '<img src="data:image/png;base64,%s">' % image_to_base64(img, image['format'])
    
    # Blue HTML
    img.putdata([blue_pixel(pixel) for pixel in image['numpy']])
    image['html_blue'] =  '<img src="data:image/png;base64,%s">' % image_to_base64(img, image['format'])
    
    
def process_image(image, baseWidth=2048):
    image_management(image, baseWidth)
    print("---- meta data -----")
    print(image['label'])
    print(image['source'])
    print(image['format'])
    print(image['mode'])
    print("Original size: ", image['size'])
    print("Scaled size: ", image['scaled_size'])
    
    print("-- images --")
    display(HTML(image['html'])) 
    display(HTML(image['html_grey'])) 
    display(HTML(image['html_red'])) 
    display(HTML(image['html_green'])) 
    display(HTML(image['html_blue'])) 


## Sequential Processing 
> The for loop iterates over the list of images and processes them one at a time, in order.

In [ ]:
# Jupyter Notebook Visualization of Images
if __name__ == "__main__":
    # setup default images
    images = image_data()

    # Sequential Processing    
    for image in images:
        process_image(image)
        
    print()

## Parallel Computing

 > In parallel or concurrent mode, the ThreadPoolExecutor is used to submit each image to a separate worker thread, allowing multiple images to be processed simultaneously. Multithreading allows multiple concurrent tasks of a process at the same time. The executor.map() method is used to apply the process_image function to each image in the images list.  
 - The order in which the images are processed is not guaranteed, as threads are performed simultaneously.

In [ ]:
import concurrent.futures

# Jupyter Notebook Visualization of Images
if __name__ == "__main__":
    # setup default images
    images = image_data()
    
    # Parallel Processsing
    # executor allocates threads, it considers core execution capability of machine
    with concurrent.futures.ThreadPoolExecutor() as executor:
        executor.map(process_image, images)  # order is not predictable
        
    print()

## Observing Parallel Computing and Threads
> You can observe Processes, CPU Percentage, and Threads with Tools on your machine. Common tools to monitor performance are Activity Monitor on MacOS or Task Manager on Windows.   

- This example is using ```top``` launched in VSCode Terminal.
![](images/top.png)
    - PID is Process ID.  
    - COMMAND is task running on machine.  Python is activated when running this Jupyter notebook.
    - #TH is number of threads.   This increases from 15/1 to 18/1 on my machine when running python parallel computing example.


## Hacks
> AP Classroom. Provide answers and thoughts on theoritical question form college board Video in section 4.3.  They start at about the 9 minute mark.
- Example 1
- Example 2

> Data Structures.  Build a List Comprehension example
- list = [calc(item) for item in items]

In [4]:
import random
import time
list = [1, 5, 6, 4, 3, 7, 2, 8]
list2 = [51, 53, 52, 56, 54, 55, 57, 58]
list3 = [1000, 34873, 23872, 655906, 16251, 23244, 12, 1231131]
lists = [list, list2, list3]
finished = []

def isSorted(list):
    for i in range(len(list) - 1):
        if (list[i+1] < list[i]):
            return False
    return True

def bogosort(list):
    i = 0
    global finished
    finish = []
    while(not isSorted(list)):
        i += 1
        random.shuffle(list)
        print(i, end=" ")
        print(list)
    finish.append([i, list])
    finished.append([i, list])
    return finish

def bogosortLists(lists):
    finalList = []
    for list in lists:
        finalList.append(bogosort(list))
    return finalList

#sequential
def sequentialComputing():
    for list in bogosortLists(lists=lists):
        print(list)

# paralell
def paralellComputing(lists):
    import concurrent.futures

    with concurrent.futures.ThreadPoolExecutor() as executor:
        executor.map(bogosort, lists)

        global finished   
        for list in finished:
            print(list)

In [2]:
sequentialComputing()

1 [1, 3, 2, 7, 8, 4, 5, 6]
2 [7, 2, 3, 6, 4, 8, 5, 1]
3 [8, 7, 1, 5, 4, 3, 6, 2]
4 [6, 3, 2, 8, 1, 5, 4, 7]
5 [1, 4, 8, 2, 7, 5, 3, 6]
6 [1, 3, 4, 8, 6, 5, 7, 2]
7 [6, 5, 4, 8, 2, 3, 7, 1]
8 [8, 7, 3, 4, 2, 1, 5, 6]
9 [7, 1, 3, 2, 6, 8, 4, 5]
10 [3, 8, 2, 5, 6, 7, 4, 1]
11 [2, 1, 5, 7, 3, 4, 6, 8]
12 [5, 7, 6, 8, 3, 4, 2, 1]
13 [4, 5, 6, 8, 3, 7, 2, 1]
14 [7, 5, 8, 2, 1, 6, 3, 4]
15 [2, 8, 4, 3, 7, 1, 5, 6]
16 [2, 4, 5, 8, 3, 1, 7, 6]
17 [8, 3, 1, 4, 7, 6, 5, 2]
18 [5, 2, 3, 6, 4, 1, 7, 8]
19 [5, 7, 8, 2, 4, 6, 1, 3]
20 [6, 2, 3, 5, 8, 1, 7, 4]
21 [7, 3, 1, 5, 4, 2, 6, 8]
22 [4, 2, 8, 1, 6, 3, 5, 7]
23 [6, 4, 7, 2, 5, 8, 1, 3]
24 [2, 7, 3, 1, 8, 4, 5, 6]
25 [2, 5, 6, 3, 7, 4, 1, 8]
26 [6, 7, 2, 4, 3, 8, 5, 1]
27 [3, 4, 2, 6, 1, 7, 8, 5]
28 [5, 8, 7, 3, 4, 2, 6, 1]
29 [8, 2, 1, 7, 4, 6, 3, 5]
30 [2, 4, 6, 1, 7, 8, 3, 5]
31 [8, 3, 7, 6, 4, 2, 5, 1]
32 [3, 6, 8, 4, 2, 7, 1, 5]
33 [5, 8, 2, 7, 3, 1, 4, 6]
34 [6, 7, 3, 4, 5, 2, 1, 8]
35 [4, 8, 2, 5, 1, 3, 6, 7]
36 [1, 6, 3, 5, 8, 7, 4, 2]
3

In [5]:
paralellComputing(lists=lists)

1 [4, 2, 6, 3, 1, 8, 7, 5]
2 [4, 1, 3, 7, 5, 2, 6, 8]
3 [2, 3, 4, 6, 7, 5, 1, 8]
4 [4, 8, 3, 5, 1, 6, 7, 2]
5 [1, 2, 3, 8, 4, 7, 5, 6]
6 [5, 6, 8, 2, 4, 3, 1, 7]
7 [1, 4, 5, 7, 2, 3, 6, 8]
8 [3, 8, 5, 7, 2, 1, 4, 6]
9 [6, 3, 5, 2, 7, 4, 1, 8]
10 [2, 4, 5, 8, 3, 6, 7, 1]
11 [5, 8, 7, 3, 4, 1, 6, 2]
12 [2, 7, 8, 3, 1, 4, 5, 6]
13 [1, 7, 3, 6, 8, 2, 5, 4]
14 [2, 1, 5, 7, 6, 4, 3, 8]
15 [2, 5, 8, 3, 7, 1, 6, 4]
16 [6, 4, 2, 5, 3, 7, 8, 1]
17 [4, 6, 1, 3, 8, 5, 7, 2]
18 [6, 8, 7, 1, 2, 4, 3, 5]
19 [6, 8, 4, 5, 7, 2, 3, 1]
20 [5, 3, 1, 7, 8, 4, 6, 2]
21 [3, 1, 5, 7, 2, 6, 4, 8]
22 [8, 2, 1, 6, 7, 3, 5, 4]
23 [4, 7, 5, 3, 6, 1, 8, 2]
24 [7, 6, 5, 8, 2, 4, 1, 3]
25 [3, 7, 8, 4, 1, 5, 2, 6]
26 [5, 7, 4, 2, 3, 8, 6, 1]
27 [6, 2, 7, 1, 3, 4, 8, 5]
28 [4, 1, 2, 5, 6, 7, 8, 3]
29 [7, 4, 6, 3, 2, 8, 1, 5]
30 [8, 1, 5, 6, 4, 3, 2, 7]
31 [1, 6, 2, 3, 7, 8, 4, 5]
32 [3, 1, 8, 4, 7, 6, 2, 5]
33 [3, 2, 4, 5, 8, 6, 1, 7]
34 [3, 1, 4, 6, 5, 2, 7, 8]
35 [5, 1, 4, 7, 6, 2, 8, 3]
36 [8, 7, 4, 2, 6, 1, 5, 3]
3